In [1]:
import pandas as pd
import panel as pn
import matplotlib.pyplot as plt
import folium
from folium.plugins import HeatMap
from dashboard_energia.transformacion.transformacion import transformar_columnas as trans_col, antiguamiento_luminarias as antig_lum    
from folium.plugins import MarkerCluster
from io import BytesIO
import geopandas as gpd
from shapely.geometry import Point
import plotly.graph_objects as go
import plotly.express as px
pn.extension("plotly")


C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2101411117.py:13: UserWarning: Using Panel interactively in VSCode notebooks requires the jupyter_bokeh package to be installed. You can install it with:

   pip install jupyter_bokeh

or:
    conda install jupyter_bokeh

and try again.
  pn.extension("plotly")


In [2]:
# Cargar datos
df = pd.read_csv("dashboard_energia/data/EQUIPO_AP_LUMINARIA.csv", encoding="utf-8")

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2065602223.py:2: DtypeWarning: Columns (3,4,5,13) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("dashboard_energia/data/EQUIPO_AP_LUMINARIA.csv", encoding="utf-8")


In [3]:

#tranformamos las columnas
antig_lum(trans_col(df))

FECHA_CORTE FECHA_EMISION CODEMP  CODLUMINARIA    CODTRAMOBT  \
0        2025-06-18    2023-12-31   SEAL  ATO000001581  VBT000108575   
1        2025-06-18    2023-12-31   SEAL  ATO000001630  VBT000063148   
2        2025-06-18    2023-12-31   SEAL  ATO000001632  VBT000182767   
3        2025-06-18    2023-12-31   SEAL  ATO000001659  VBT000113803   
4        2025-06-18    2023-12-31   SEAL  ATO000001726  VBT000063872   
...             ...           ...    ...           ...           ...   
2356763  2025-06-18    2023-12-31   ELPU  EAP000087460  TBA000125419   
2356764  2025-06-18    2023-12-31   ELPU  EAP000057596  TBT000079211   
2356765  2025-06-18    2023-12-31   ELPU  EAP000057580  TBT000113333   
2356766  2025-06-18    2023-12-31   ELPU  EAP000019256  TBT000043760   
2356767  2025-06-18    2023-12-31   ELPU  EAP000019264  TBT000043767   

             CODTRAMOVIA                               DESCRIPCION_PASTORAL  \
0                1046792  PASTORAL METALICO SIMPLE DE 3,2 m x 1,5 pulg D...   
1                1282305  PASTORAL METALICO SIMPLE DE 3,4 m x 2 pulg DE ...   
2                1282305  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   
3                1270015  PASTORAL METALICO SIMPLE DE 3,2 m x 1,5 pulg D...   
4                1270175                          CONCRETO SIMPLE DE 1,30 m   
...                  ...                                                ...   
2356763  No especificado  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   
2356764  No especificado  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   
2356765  No especificado  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   
2356766  No especificado  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   
2356767  No especificado  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...   

             PROPIEDAD FECPUESTASERVICIO SECTOR COD_SISTEMA_ELECTRICO  \
0        Distribuidora        2022-11-19      2                SE0134   
1        Distribuidora        2022-10-05      2                SE0134   
2        Distribuidora        2022-10-05      2                SE0134   
3        Distribuidora        2023-05-31      2                SE0134   
4        Distribuidora        2022-11-18      2                SE0134   
...                ...               ...    ...                   ...   
2356763  Distribuidora        2018-08-20      7                 SR029   
2356764  Distribuidora        2011-09-19      7                 SR037   
2356765  Distribuidora        2011-09-19      7                 SR037   
2356766  Distribuidora        2010-11-12      7                 SR030   
2356767  Distribuidora        2010-11-12      7                 SR030   

                                  NOMBRE_SISTEMA_ELECTRICO   ALIMENTADOR  \
0                                                 Arequipa      COMERCIO   
1                                                 Arequipa  INDEPENDENCI   
2                                                 Arequipa    MARIATEGUI   
3                                                 Arequipa      QUEQUENA   
4                                                 Arequipa      QUEQUENA   
...                                                    ...           ...   
2356763  Electrificaci?n Rural Lote N 02 SER Mazocruz I...       1092018   
2356764  Ampliaci?n de Electrificaci?n Rural del Distri...      GRUPO 12   
2356765  Ampliaci?n de Electrificaci?n Rural del Distri...      GRUPO 12   
2356766  Construcci?n Pequeno Sistema El?ctrico de la C...       1162011   
2356767  Construcci?n Pequeno Sistema El?ctrico de la C...       1162011   

        SUBESTACION  COORDENADA_X  COORDENADA_Y  ANTIGUEDAD RANGO_ANTIGUEDAD  
0              1815    -71.585212    -16.380081           2         0-4 años  
1              1277    -71.524104    -16.364576           2         0-4 años  
2              3439    -71.522991    -16.363806           2         0-4 años  
3              1918    -71.455706    -16.570025           2         0-4 años  
4        

In [4]:
# Crear geometría de puntos
geometry = [Point(xy) for xy in zip(df["COORDENADA_X"], df["COORDENADA_Y"])]
gdf_luminarias = gpd.GeoDataFrame(df, geometry=geometry, crs="EPSG:4326")  # WGS84

gdf_distritos = gpd.read_file("dashboard_energia/data/DISTRITOS.shp")  # INEI o MIDIS
gdf_distritos = gdf_distritos.to_crs("EPSG:4326")  # Asegura que ambos estén en el mismo CRS

gdf_intersectado = gpd.sjoin(gdf_luminarias, gdf_distritos, how="inner", predicate="intersects")


In [5]:
print(gdf_intersectado.head())
print(gdf_intersectado.columns)

  FECHA_CORTE FECHA_EMISION CODEMP  CODLUMINARIA    CODTRAMOBT CODTRAMOVIA  \
0  2025-06-18    2023-12-31   SEAL  ATO000001581  VBT000108575     1046792   
1  2025-06-18    2023-12-31   SEAL  ATO000001630  VBT000063148     1282305   
2  2025-06-18    2023-12-31   SEAL  ATO000001632  VBT000182767     1282305   
3  2025-06-18    2023-12-31   SEAL  ATO000001659  VBT000113803     1270015   
4  2025-06-18    2023-12-31   SEAL  ATO000001726  VBT000063872     1270175   

                                DESCRIPCION_PASTORAL      PROPIEDAD  \
0  PASTORAL METALICO SIMPLE DE 3,2 m x 1,5 pulg D...  Distribuidora   
1  PASTORAL METALICO SIMPLE DE 3,4 m x 2 pulg DE ...  Distribuidora   
2  PASTORAL METALICO SIMPLE DE 1,5 m x 1,5 pulg D...  Distribuidora   
3  PASTORAL METALICO SIMPLE DE 3,2 m x 1,5 pulg D...  Distribuidora   
4                          CONCRETO SIMPLE DE 1,30 m  Distribuidora   

  FECPUESTASERVICIO SECTOR  ... OBJECTID_1  UBIGEO CODDEP DEPARTAMEN  CODPROV  \
0        2022-11-19    

In [6]:
df_poblacion = pd.read_csv("dashboard_energia/data/dato-poblacion.csv", encoding="ISO-8859-1", sep=";")

df_poblacion["UBIGEO"] = df_poblacion["UBIGEO"].astype(str).str.zfill(6)

df_combinado = gdf_intersectado.merge(df_poblacion, on="UBIGEO", how="left")


In [7]:
print(df_combinado.columns)

Index(['FECHA_CORTE_x', 'FECHA_EMISION', 'CODEMP', 'CODLUMINARIA',
       'CODTRAMOBT', 'CODTRAMOVIA', 'DESCRIPCION_PASTORAL', 'PROPIEDAD',
       'FECPUESTASERVICIO', 'SECTOR', 'COD_SISTEMA_ELECTRICO',
       'NOMBRE_SISTEMA_ELECTRICO', 'ALIMENTADOR', 'SUBESTACION',
       'COORDENADA_X', 'COORDENADA_Y', 'ANTIGUEDAD', 'geometry', 'index_right',
       'OBJECTID_1', 'UBIGEO', 'CODDEP', 'DEPARTAMEN', 'CODPROV',
       'PROVINCIA_x', 'CODDIST', 'DISTRITO_x', 'CAPITAL', 'FUENTE',
       'FECHA_CORTE_y', 'ANIO', 'DEPARTAMENTO', 'PROVINCIA_y', 'DISTRITO_y',
       'REGION_NATURAL', 'TIPO_MUNICIPALIDAD', 'POB_TOTAL_INEI',
       'POB_URBANA_INEI', 'POB_RURAL_INEI', 'CLASIFICACION_MUNICIPAL_MEF',
       'GENERACION_PER_CAPITA_DOM', 'GENERACION_DOM_URBANA_TDIA',
       'GENERACION_DOM URBANA_TANIO', 'GENERACION_MUN_TANIO',
       'GENERACION_MUN_TDIA', 'GENERACION_PER_CAPITA_MUNICIPAL'],
      dtype='object')


In [40]:
#Agrupamos y agregamos
df_grouped = df_combinado.groupby(['UBIGEO', 'DISTRITO_x']).agg({
    'CODLUMINARIA': 'count',
    'ANTIGUEDAD': 'mean',
    'POB_TOTAL_INEI': 'mean',
    'POB_RURAL_INEI': 'mean',
    'TIPO_MUNICIPALIDAD': 'first',
    'CAPITAL': 'first',
    'REGION_NATURAL': 'first',
    'CODEMP': 'first',
    'DESCRIPCION_PASTORAL': 'first'
}).rename(columns={'CODLUMINARIA': 'N_LUMINARIAS'})

print(df_grouped.head())


                    N_LUMINARIAS  ANTIGUEDAD  POB_TOTAL_INEI  POB_RURAL_INEI  \
UBIGEO DISTRITO_x                                                              
010101 CHACHAPOYAS          3077    7.250569         40824.0           965.0   
010102 ASUNCION                8    9.000000           273.0           142.0   
010103 BALSAS                 76    8.315789          1147.0           869.0   
010104 CHETO                  27    1.888889           709.0           264.0   
010105 CHILIQUIN              21    8.571429           568.0           422.0   

                   TIPO_MUNICIPALIDAD      CAPITAL REGION_NATURAL CODEMP  \
UBIGEO DISTRITO_x                                                          
010101 CHACHAPOYAS         PROVINCIAL  CHACHAPOYAS          SELVA   ELOR   
010102 ASUNCION             DISTRITAL     ASUNCION          SELVA   ELOR   
010103 BALSAS               DISTRITAL       BALSAS         SIERRA   ELOR   
010104 CHETO                DISTRITAL        CHETO         

In [47]:
# Indicadores derivados:
df_grouped['LUMINARIAS_POR_1000HAB'] = df_grouped['N_LUMINARIAS'] / df_grouped['POB_TOTAL_INEI'] * 1000
df_grouped['%POB_RURAL'] = df_grouped['POB_RURAL_INEI'] / df_grouped['POB_TOTAL_INEI'] * 100

print(df_grouped.head())

                    N_LUMINARIAS  ANTIGUEDAD  POB_TOTAL_INEI  POB_RURAL_INEI  \
UBIGEO DISTRITO_x                                                              
010101 CHACHAPOYAS          3077    7.250569         40824.0           965.0   
010102 ASUNCION                8    9.000000           273.0           142.0   
010103 BALSAS                 76    8.315789          1147.0           869.0   
010104 CHETO                  27    1.888889           709.0           264.0   
010105 CHILIQUIN              21    8.571429           568.0           422.0   

                   TIPO_MUNICIPALIDAD      CAPITAL REGION_NATURAL CODEMP  \
UBIGEO DISTRITO_x                                                          
010101 CHACHAPOYAS         PROVINCIAL  CHACHAPOYAS          SELVA   ELOR   
010102 ASUNCION             DISTRITAL     ASUNCION          SELVA   ELOR   
010103 BALSAS               DISTRITAL       BALSAS         SIERRA   ELOR   
010104 CHETO                DISTRITAL        CHETO         

In [49]:
distritos = gpd.read_file('dashboard_energia/data/limites/Limite Distrital INEI 2025 CPV.shp').to_crs('EPSG:32718')
distritos['AREA_KM2'] = distritos['geometry'].area / 1e6

# 2. Reproyectar a lat/lon para visualización
distritos = distritos.to_crs('EPSG:4326')

# 3. Unir con indicadores
df_final = distritos.merge(df_grouped, on='UBIGEO')
df_final['LUMINARIAS_POR_KM2'] = df_final['N_LUMINARIAS'] / df_final['AREA_KM2']

df_final['geometry'] = df_final['geometry'].simplify(0.001, preserve_topology=True)



In [57]:
def choropleth(indicador):
    fig = px.choropleth_mapbox(
        df_final,
        geojson=df_final.geometry,
        locations=df_final.index,
        color=indicador,
        hover_name='DISTRITO',
        center={"lat": -9.19, "lon": -75.015},
        zoom=5,
        color_continuous_scale=["#ffffcc", "#ffeda0", "#feb24c", "#f03b20", "#bd0026"],
        mapbox_style="carto-positron"
    )
    return pn.pane.Plotly(fig, config={'responsive': True})

In [58]:
choropleth("ANTIGUEDAD")

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2892510256.py:2: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



Plotly(Figure, config={'responsive': True})

In [ ]:
import panel as pn
pn.extension('plotly')

# Selectores dinámicos
selector_indicador = pn.widgets.Select(
    name='Indicador',
    options={
        'Antigüedad promedio': 'ANTIGUEDAD',
        'Luminarias por 1000 hab': 'LUMINARIAS_POR_1000HAB',
        'Densidad por km²': 'LUMINARIAS_POR_KM2'
    }
)

selector_municipio = pn.widgets.MultiSelect(
    name='Tipo de municipio',
    options=list(df_final['TIPO_MUNICIPALIDAD'].unique()),
    value=list(df_final['TIPO_MUNICIPALIDAD'].unique())
)

selector_region = pn.widgets.MultiSelect(
    name='Región natural',
    options=list(df_final['REGION_NATURAL'].unique()),
    value=list(df_final['REGION_NATURAL'].unique())
)

selector_emp = pn.widgets.MultiSelect(
    name='Empresa',
    options=list(df_final['CODEMP'].unique()),
    value=list(df_final['CODEMP'].unique())
)

# Filtro reactivo
@pn.depends(selector_indicador, selector_municipio, selector_region, selector_emp)
def update_map(indicador, municipios, regiones, empresa):
    df_filtrado = df_final[
        df_final['TIPO_MUNICIPALIDAD'].isin(municipios) &
        df_final['REGION_NATURAL'].isin(regiones)&
        df_final['CODEMP'].isin(empresa) 

    ]
    
    fig = px.choropleth_mapbox(
        df_filtrado,
        geojson=df_filtrado.geometry,
        locations=df_filtrado.index,
        color=indicador,
        hover_name='DISTRITO',
        center={"lat": -9.19, "lon": -75.015},
        zoom=5,
        color_continuous_scale="Reds",
        mapbox_style="carto-positron"
    )
    return pn.pane.Plotly(fig, config={'responsive': True})

# Layout del dashboard
dashboard = pn.Column(
    "# 🗺️ Dashboard de cobertura energética",
    pn.Row(selector_indicador, selector_municipio, selector_region, selector_emp),
    update_map
)

dashboard.servable()
pn.serve(dashboard)


C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:2: UserWarning:

Using Panel interactively in VSCode notebooks requires the jupyter_bokeh package to be installed. You can install it with:

   pip install jupyter_bokeh

or:
    conda install jupyter_bokeh

and try again.



C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/



Launching server at http://localhost:52924


C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropleth_map* instead. Learn more at: https://plotly.com/python/mapbox-to-maplibre/

C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\2558844518.py:42: DeprecationWarning:

*choropleth_mapbox* is deprecated! Use *choropl

In [60]:
import panel as pn
pn.extension('plotly')

indicadores = ['LUMINARIAS_POR_1000HAB', 'LUMINARIAS_POR_KM2', 'ANTIGÜEDAD', '%POB_RURAL']
selector = pn.widgets.Select(name='Indicador ODS 7', options=indicadores)


C:\Users\ymnl_\AppData\Local\Temp\ipykernel_15504\796633410.py:2: UserWarning:

Using Panel interactively in VSCode notebooks requires the jupyter_bokeh package to be installed. You can install it with:

   pip install jupyter_bokeh

or:
    conda install jupyter_bokeh

and try again.

